In [1]:
import requests 
import json
import pandas as pd
import numpy as np

In [2]:
pd.set_option('display.max_columns', None)  # or 1000
pd.set_option('display.max_rows', None)  # or 1000
pd.set_option('display.max_colwidth', -1)  # or 199

<ipython-input-2-6dacdb3ef330>:3: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('display.max_colwidth', -1)  # or 199


In [3]:
api_header = {
    'api-key': 'b60192d669b35ccaf0693cb1a0775856'
}

In [4]:
def book_list(api):
    book_list_payload = {}
    book_array = []
    book_list_url = "https://api.scripture.api.bible/v1/bibles/06125adad2d5898a-01/books?include-chapters=" \
                    "false&include-chapters-and-sections=false"
    book_list_response = requests.request("GET", book_list_url, headers=api, data=book_list_payload)
    book_list_response_json = json.loads(book_list_response.text)

    for item in book_list_response_json["data"]:
        book_array.append(item["id"])

    return book_array

In [5]:

def book_chapters(api, b_id):
    payload = {}
    array = []
    book_id_array = []
    ref_array = []
    url = "https://api.scripture.api.bible/v1/bibles/06125adad2d5898a-01/books/{}/chapters".format(b_id)
    response = requests.request("GET", url, headers=api, data=payload)
    response_json = json.loads(response.text)
    response_json1 = response_json["data"]
    
    for item in response_json1:
        array.append(item["id"])
    for item in response_json1:
        book_id_array.append(item["bookId"])
    for item in response_json1:
        ref_array.append(item["reference"])
        
        
    return array, book_id_array, ref_array


In [6]:
key_array = []
id_array = []
ref_array = []

for item in book_list(api_header):
    a, b, c = book_chapters(api_header, item)
    key_array.append(a)
    id_array.append(b)
    ref_array.append(c)

In [8]:
flatten_key = np.concatenate(key_array)
flatten_id = np.concatenate(id_array)
flatten_ref = np.concatenate(ref_array)

In [9]:
df = pd.DataFrame({"id": flatten_key, 
                  "bookId": flatten_id,
                  "reference": flatten_ref})

In [8]:
df.head

<bound method NDFrame.head of              id bookId      reference
0     GEN.intro    GEN        Genesis
1         GEN.1    GEN      Genesis 1
2         GEN.2    GEN      Genesis 2
3         GEN.3    GEN      Genesis 3
4         GEN.4    GEN      Genesis 4
...         ...    ...            ...
1249     REV.18    REV  Revelation 18
1250     REV.19    REV  Revelation 19
1251     REV.20    REV  Revelation 20
1252     REV.21    REV  Revelation 21
1253     REV.22    REV  Revelation 22

[1254 rows x 3 columns]>

In [10]:
book_list = df.bookId.unique()
book_list

array(['GEN', 'EXO', 'LEV', 'NUM', 'DEU', 'JOS', 'JDG', 'RUT', '1SA',
       '2SA', '1KI', '2KI', '1CH', '2CH', 'EZR', 'NEH', 'EST', 'JOB',
       'PSA', 'PRO', 'ECC', 'SNG', 'ISA', 'JER', 'LAM', 'EZK', 'DAN',
       'HOS', 'JOL', 'AMO', 'OBA', 'JON', 'MIC', 'NAM', 'HAB', 'ZEP',
       'HAG', 'ZEC', 'MAL', 'MAT', 'MRK', 'LUK', 'JHN', 'ACT', 'ROM',
       '1CO', '2CO', 'GAL', 'EPH', 'PHP', 'COL', '1TH', '2TH', '1TI',
       '2TI', 'TIT', 'PHM', 'HEB', 'JAS', '1PE', '2PE', '1JN', '2JN',
       '3JN', 'JUD', 'REV'], dtype=object)

In [10]:
#### Cross Reference, Data Clean up ###

dff = pd.read_table('cross.txt')
dff['Book'] = dff['From Verse'].str.split('.').str[0]
dff['chapter'] = dff['From Verse'].str.split('.').str[1]
dff['Verse'] = dff['From Verse'].str.split('.').str[-1]

In [11]:
book_list2 = dff['Book'].unique()
book_list2

array(['Gen', 'Exod', 'Lev', 'Num', 'Deut', 'Josh', 'Judg', 'Ruth',
       '1Sam', '2Sam', '1Kgs', '2Kgs', '1Chr', '2Chr', 'Ezra', 'Neh',
       'Esth', 'Job', 'Ps', 'Prov', 'Eccl', 'Song', 'Isa', 'Jer', 'Lam',
       'Ezek', 'Dan', 'Hos', 'Joel', 'Amos', 'Obad', 'Jonah', 'Mic',
       'Nah', 'Hab', 'Zeph', 'Hag', 'Zech', 'Mal', 'Matt', 'Mark', 'Luke',
       'John', 'Acts', 'Rom', '1Cor', '2Cor', 'Gal', 'Eph', 'Phil', 'Col',
       '1Thess', '2Thess', '1Tim', '2Tim', 'Titus', 'Phlm', 'Heb', 'Jas',
       '1Pet', '2Pet', '1John', '2John', '3John', 'Jude', 'Rev'],
      dtype=object)

In [12]:
# df['book'] = df['reference'].str.split(' ').str[0]
# df

In [15]:
counter = -1
for item in range(66):
    counter += 1
    dff['Book'].replace('{}'.format(book_list2[counter]),'{}'.format(book_list[counter]),inplace=True)


In [16]:
counter = -1
for item in range(66):
    counter += 1
    dff['To Verse'] = dff['To Verse'].astype(np.str).replace(to_replace='{}'.format(book_list2[counter]), value='{}'.format(book_list[counter]), regex=True)

In [17]:
dff.head()

From Verse           To Verse  Votes  #www.openbible.info CC-BY 2020-11-02  \
0    Gen.1.1  PRO.8.22-PRO.8.30     35                                   NaN   
1    Gen.1.1          EXO.31.18    -21                                   NaN   
2    Gen.1.1          JER.51.15     42                                   NaN   
3    Gen.1.1           REV.14.7     42                                   NaN   
4    Gen.1.1          ACT.14.15     39                                   NaN   

  Book chapter Verse  
0  GEN       1     1  
1  GEN       1     1  
2  GEN       1     1  
3  GEN       1     1  
4  GEN       1     1

In [18]:
dff["book_chapter"] = dff["Book"] + "." + dff["chapter"]

In [282]:
# t = dff[dff["From Verse"] == "Rom.14.17"]["To Verse"]

In [211]:
# a = []
# for item in t:
#     a.append(item)

In [452]:
# dff.columns = [["from_verse", "to_verse", "votes", "nan", "book", "chapter", "verse", "book_chapter"]]

In [19]:
dff.head(1000)

From Verse             To Verse  Votes  \
0      Gen.1.1    PRO.8.22-PRO.8.30     35   
1      Gen.1.1            EXO.31.18    -21   
2      Gen.1.1            JER.51.15     42   
3      Gen.1.1             REV.14.7     42   
4      Gen.1.1            ACT.14.15     39   
..         ...                  ...    ...   
995   Gen.3.19  JOB.17.13-JOB.17.16      3   
996   Gen.3.19            GEN.18.27      3   
997   Gen.3.19            PSA.22.29      3   
998   Gen.3.19             ECC.12.7     15   
999   Gen.3.19             ECC.3.20      5   

     #www.openbible.info CC-BY 2020-11-02 Book chapter Verse book_chapter  
0                                     NaN  GEN       1     1        GEN.1  
1                                     NaN  GEN       1     1        GEN.1  
2                                     NaN  GEN       1     1        GEN.1  
3                                     NaN  GEN       1     1        GEN.1  
4                                     NaN  GEN       1     1        GEN.1  
..                                    ...  ...     ...   ...          ...  
995                                   NaN  GEN       3    19        GEN.3  
996                                   NaN  GEN       3    19        GEN.3  
997                                   NaN  GEN       3    19        GEN.3  
998                                   NaN  GEN       3    19        GEN.3  
999                                   NaN  GEN       3    19        GEN.3  

[1000 rows x 8 columns]

In [20]:
dff['to2_verse'] = dff['To Verse'].str.split('-').str[1]


In [21]:
dff.head()

From Verse           To Verse  Votes  #www.openbible.info CC-BY 2020-11-02  \
0    Gen.1.1  PRO.8.22-PRO.8.30     35                                   NaN   
1    Gen.1.1          EXO.31.18    -21                                   NaN   
2    Gen.1.1          JER.51.15     42                                   NaN   
3    Gen.1.1           REV.14.7     42                                   NaN   
4    Gen.1.1          ACT.14.15     39                                   NaN   

  Book chapter Verse book_chapter to2_verse  
0  GEN       1     1        GEN.1  PRO.8.30  
1  GEN       1     1        GEN.1       NaN  
2  GEN       1     1        GEN.1       NaN  
3  GEN       1     1        GEN.1       NaN  
4  GEN       1     1        GEN.1       NaN

In [22]:
dff['to2_verse'] = dff['to2_verse'].str.split('.').str[-1]

In [23]:
dff.head(1000)

From Verse             To Verse  Votes  \
0      Gen.1.1    PRO.8.22-PRO.8.30     35   
1      Gen.1.1            EXO.31.18    -21   
2      Gen.1.1            JER.51.15     42   
3      Gen.1.1             REV.14.7     42   
4      Gen.1.1            ACT.14.15     39   
..         ...                  ...    ...   
995   Gen.3.19  JOB.17.13-JOB.17.16      3   
996   Gen.3.19            GEN.18.27      3   
997   Gen.3.19            PSA.22.29      3   
998   Gen.3.19             ECC.12.7     15   
999   Gen.3.19             ECC.3.20      5   

     #www.openbible.info CC-BY 2020-11-02 Book chapter Verse book_chapter  \
0                                     NaN  GEN       1     1        GEN.1   
1                                     NaN  GEN       1     1        GEN.1   
2                                     NaN  GEN       1     1        GEN.1   
3                                     NaN  GEN       1     1        GEN.1   
4                                     NaN  GEN       1     1        GEN.1   
..                                    ...  ...     ...   ...          ...   
995                                   NaN  GEN       3    19        GEN.3   
996                                   NaN  GEN       3    19        GEN.3   
997                                   NaN  GEN       3    19        GEN.3   
998                                   NaN  GEN       3    19        GEN.3   
999                                   NaN  GEN       3    19        GEN.3   

    to2_verse  
0          30  
1         NaN  
2         NaN  
3         NaN  
4         NaN  
..        ...  
995        16  
996       NaN  
997       NaN  
998       NaN  
999       NaN  

[1000 rows x 9 columns]

In [524]:
dff["to_verse"] = dff.to2_verse.fillna('')

In [24]:
tt = dff[dff["To Verse"].str.contains("-")]
tt
for item in tt:
    dff['To Verse'] = dff['To Verse'].str.split('-').str[0]

In [25]:
dff.head(1000)

From Verse   To Verse  Votes  #www.openbible.info CC-BY 2020-11-02 Book  \
0      Gen.1.1   PRO.8.22     35                                   NaN  GEN   
1      Gen.1.1  EXO.31.18    -21                                   NaN  GEN   
2      Gen.1.1  JER.51.15     42                                   NaN  GEN   
3      Gen.1.1   REV.14.7     42                                   NaN  GEN   
4      Gen.1.1  ACT.14.15     39                                   NaN  GEN   
..         ...        ...    ...                                   ...  ...   
995   Gen.3.19  JOB.17.13      3                                   NaN  GEN   
996   Gen.3.19  GEN.18.27      3                                   NaN  GEN   
997   Gen.3.19  PSA.22.29      3                                   NaN  GEN   
998   Gen.3.19   ECC.12.7     15                                   NaN  GEN   
999   Gen.3.19   ECC.3.20      5                                   NaN  GEN   

    chapter Verse book_chapter to2_verse  
0         1     1        GEN.1        30  
1         1     1        GEN.1       NaN  
2         1     1        GEN.1       NaN  
3         1     1        GEN.1       NaN  
4         1     1        GEN.1       NaN  
..      ...   ...          ...       ...  
995       3    19        GEN.3        16  
996       3    19        GEN.3       NaN  
997       3    19        GEN.3       NaN  
998       3    19        GEN.3       NaN  
999       3    19        GEN.3       NaN  

[1000 rows x 9 columns]

In [31]:
ttt = dff[~dff["to2_verse"].isnull()]
for item in ttt:
    dff["to_verse"] = dff["To Verse"] + "-" + dff["to2_verse"]

In [34]:
dff["to_verse"].fillna(dff['To Verse'], inplace=True)


In [38]:
dff.head(100)

From Verse    To Verse  Votes  #www.openbible.info CC-BY 2020-11-02 Book  \
0   Gen.1.1    PRO.8.22    35    NaN                                    GEN   
1   Gen.1.1    EXO.31.18  -21    NaN                                    GEN   
2   Gen.1.1    JER.51.15   42    NaN                                    GEN   
3   Gen.1.1    REV.14.7    42    NaN                                    GEN   
4   Gen.1.1    ACT.14.15   39    NaN                                    GEN   
5   Gen.1.1    PSA.33.6    33    NaN                                    GEN   
6   Gen.1.1    ISA.51.16   34    NaN                                    GEN   
7   Gen.1.1    1JHN.1.1    29    NaN                                    GEN   
8   Gen.1.1    HEB.1.2     36    NaN                                    GEN   
9   Gen.1.1    PSA.136.5   40    NaN                                    GEN   
10  Gen.1.1    ISA.40.26   34    NaN                                    GEN   
11  Gen.1.1    PSA.134.3   32    NaN                                    GEN   
12  Gen.1.1    ROM.11.36   32    NaN                                    GEN   
13  Gen.1.1    PSA.102.25  37    NaN                                    GEN   
14  Gen.1.1    PRO.16.4    32    NaN                                    GEN   
15  Gen.1.1    1CO.8.6     38    NaN                                    GEN   
16  Gen.1.1    HEB.1.10    91    NaN                                    GEN   
17  Gen.1.1    PSA.121.2   34    NaN                                    GEN   
18  Gen.1.1    JER.32.17   44    NaN                                    GEN   
19  Gen.1.1    JER.10.12   40    NaN                                    GEN   
20  Gen.1.1    ISA.65.17   24    NaN                                    GEN   
21  Gen.1.1    PSA.96.5    32    NaN                                    GEN   
22  Gen.1.1    PSA.89.11   32    NaN                                    GEN   
23  Gen.1.1    REV.22.13   22    NaN                                    GEN   
24  Gen.1.1    REV.21.6    25    NaN                                    GEN   
25  Gen.1.1    JHN.1.1     163   NaN                                    GEN   
26  Gen.1.1    PSA.104.24  32    NaN                                    GEN   
27  Gen.1.1    1CH.16.26   27    NaN                                    GEN   
28  Gen.1.1    REV.10.6    33    NaN                                    GEN   
29  Gen.1.1    MRK.13.19   25    NaN                                    GEN   
30  Gen.1.1    ISA.40.28   37    NaN                                    GEN   
31  Gen.1.1    PSA.90.2    32    NaN                                    GEN   
32  Gen.1.1    PSA.115.15  40    NaN                                    GEN   
33  Gen.1.1    NEH.9.6     55    NaN                                    GEN   
34  Gen.1.1    ISA.44.24   49    NaN                                    GEN   
35  Gen.1.1    EXO.20.11   78    NaN                                    GEN   
36  Gen.1.1    JOB.38.4    83    NaN                                    GEN   
37  Gen.1.1    JOB.26.13   22    NaN                                    GEN   
38  Gen.1.1    MAT.11.25   5     NaN                                    GEN   
39  Gen.1.1    2PE.3.5     54    NaN                                    GEN   
40  Gen.1.1    HEB.11.3    141   NaN                                    GEN   
41  Gen.1.1    ACT.17.24   74    NaN                                    GEN   
42  Gen.1.1    COL.1.16    78    NaN                                    GEN   
43  Gen.1.1    PSA.33.9    40    NaN                                    GEN   
44  Gen.1.1    ECC.12.1    11    NaN                                    GEN   
45  Gen.1.1    REV.4.11    97    NaN                                    GEN   
46  Gen.1.1    ROM.1.19    29    NaN                                    GEN   
47  Gen.1.1    ISA.37.16   34    NaN                                    GEN   
48  Gen.1.1    PSA.8.3     35    NaN                                    GEN   
49  Gen.1.1    PSA.124.8   34    NaN                 

In [39]:
dff.to_csv("cross.csv", encoding='utf-8', index=False)

In [112]:
## Now load from cross.csv, saved work from cleaning data ##
df = pd.read_csv("cross.csv")

In [113]:
df.head(100)

From Verse    To Verse  Votes  #www.openbible.info CC-BY 2020-11-02 Book  \
0   Gen.1.1    PRO.8.22    35    NaN                                    GEN   
1   Gen.1.1    EXO.31.18  -21    NaN                                    GEN   
2   Gen.1.1    JER.51.15   42    NaN                                    GEN   
3   Gen.1.1    REV.14.7    42    NaN                                    GEN   
4   Gen.1.1    ACT.14.15   39    NaN                                    GEN   
5   Gen.1.1    PSA.33.6    33    NaN                                    GEN   
6   Gen.1.1    ISA.51.16   34    NaN                                    GEN   
7   Gen.1.1    1JHN.1.1    29    NaN                                    GEN   
8   Gen.1.1    HEB.1.2     36    NaN                                    GEN   
9   Gen.1.1    PSA.136.5   40    NaN                                    GEN   
10  Gen.1.1    ISA.40.26   34    NaN                                    GEN   
11  Gen.1.1    PSA.134.3   32    NaN                                    GEN   
12  Gen.1.1    ROM.11.36   32    NaN                                    GEN   
13  Gen.1.1    PSA.102.25  37    NaN                                    GEN   
14  Gen.1.1    PRO.16.4    32    NaN                                    GEN   
15  Gen.1.1    1CO.8.6     38    NaN                                    GEN   
16  Gen.1.1    HEB.1.10    91    NaN                                    GEN   
17  Gen.1.1    PSA.121.2   34    NaN                                    GEN   
18  Gen.1.1    JER.32.17   44    NaN                                    GEN   
19  Gen.1.1    JER.10.12   40    NaN                                    GEN   
20  Gen.1.1    ISA.65.17   24    NaN                                    GEN   
21  Gen.1.1    PSA.96.5    32    NaN                                    GEN   
22  Gen.1.1    PSA.89.11   32    NaN                                    GEN   
23  Gen.1.1    REV.22.13   22    NaN                                    GEN   
24  Gen.1.1    REV.21.6    25    NaN                                    GEN   
25  Gen.1.1    JHN.1.1     163   NaN                                    GEN   
26  Gen.1.1    PSA.104.24  32    NaN                                    GEN   
27  Gen.1.1    1CH.16.26   27    NaN                                    GEN   
28  Gen.1.1    REV.10.6    33    NaN                                    GEN   
29  Gen.1.1    MRK.13.19   25    NaN                                    GEN   
30  Gen.1.1    ISA.40.28   37    NaN                                    GEN   
31  Gen.1.1    PSA.90.2    32    NaN                                    GEN   
32  Gen.1.1    PSA.115.15  40    NaN                                    GEN   
33  Gen.1.1    NEH.9.6     55    NaN                                    GEN   
34  Gen.1.1    ISA.44.24   49    NaN                                    GEN   
35  Gen.1.1    EXO.20.11   78    NaN                                    GEN   
36  Gen.1.1    JOB.38.4    83    NaN                                    GEN   
37  Gen.1.1    JOB.26.13   22    NaN                                    GEN   
38  Gen.1.1    MAT.11.25   5     NaN                                    GEN   
39  Gen.1.1    2PE.3.5     54    NaN                                    GEN   
40  Gen.1.1    HEB.11.3    141   NaN                                    GEN   
41  Gen.1.1    ACT.17.24   74    NaN                                    GEN   
42  Gen.1.1    COL.1.16    78    NaN                                    GEN   
43  Gen.1.1    PSA.33.9    40    NaN                                    GEN   
44  Gen.1.1    ECC.12.1    11    NaN                                    GEN   
45  Gen.1.1    REV.4.11    97    NaN                                    GEN   
46  Gen.1.1    ROM.1.19    29    NaN                                    GEN   
47  Gen.1.1    ISA.37.16   34    NaN                                    GEN   
48  Gen.1.1    PSA.8.3     35    NaN                                    GEN   
49  Gen.1.1    PSA.124.8   34    NaN                 

In [96]:
def book_names(api):
    book_list_payload = {}
    book_array = []
    book_list_url = "https://api.scripture.api.bible/v1/bibles/06125adad2d5898a-01/books?include-chapters=" \
                    "false&include-chapters-and-sections=false"
    book_list_response = requests.request("GET", book_list_url, headers=api, data=book_list_payload)
    book_list_response_json = json.loads(book_list_response.text)

    for item in book_list_response_json["data"]:
        # case = {"id": item["id"], "name": item["name"]}
        book_array.append(item["name"])
        # book_array.append(case)
    return book_array
book_names_final = book_names(api_header)

ConnectionError: HTTPSConnectionPool(host='api.scripture.api.bible', port=443): Max retries exceeded with url: /v1/bibles/06125adad2d5898a-01/books?include-chapters=false&include-chapters-and-sections=false (Caused by NewConnectionError('<urllib3.connection.HTTPSConnection object at 0x7f5ae9306820>: Failed to establish a new connection: [Errno -3] Temporary failure in name resolution'))

In [97]:
book_names_final[-2]
# book_list

'Jude'

In [32]:
## the goal is to have a column that give an example of "Genesis 1:6" to display on the button 

In [114]:
df['to_verse3'] = df['to_verse']

In [115]:
df['to_verse3'] = df['to_verse3'].str.split('.').str[0]

In [116]:
df.head()

From Verse   To Verse  Votes  #www.openbible.info CC-BY 2020-11-02 Book  \
0  Gen.1.1    PRO.8.22   35    NaN                                    GEN   
1  Gen.1.1    EXO.31.18 -21    NaN                                    GEN   
2  Gen.1.1    JER.51.15  42    NaN                                    GEN   
3  Gen.1.1    REV.14.7   42    NaN                                    GEN   
4  Gen.1.1    ACT.14.15  39    NaN                                    GEN   

   chapter  Verse book_chapter  to2_verse     to_verse to_verse3  
0  1        1      GEN.1        30.0       PRO.8.22-30  PRO       
1  1        1      GEN.1       NaN         EXO.31.18    EXO       
2  1        1      GEN.1       NaN         JER.51.15    JER       
3  1        1      GEN.1       NaN         REV.14.7     REV       
4  1        1      GEN.1       NaN         ACT.14.15    ACT

In [117]:
counter = -1
for item in range(66):
    counter += 1
    df['to_verse3'].replace('{}'.format(book_list[counter]),'{}'.format(book_names_final[counter]),inplace=True)


In [118]:
df.head()

From Verse   To Verse  Votes  #www.openbible.info CC-BY 2020-11-02 Book  \
0  Gen.1.1    PRO.8.22   35    NaN                                    GEN   
1  Gen.1.1    EXO.31.18 -21    NaN                                    GEN   
2  Gen.1.1    JER.51.15  42    NaN                                    GEN   
3  Gen.1.1    REV.14.7   42    NaN                                    GEN   
4  Gen.1.1    ACT.14.15  39    NaN                                    GEN   

   chapter  Verse book_chapter  to2_verse     to_verse   to_verse3  
0  1        1      GEN.1        30.0       PRO.8.22-30  Proverbs    
1  1        1      GEN.1       NaN         EXO.31.18    Exodus      
2  1        1      GEN.1       NaN         JER.51.15    Jeremiah    
3  1        1      GEN.1       NaN         REV.14.7     Revelation  
4  1        1      GEN.1       NaN         ACT.14.15    Acts

In [119]:
df['to_verse4'] = df['to_verse']

In [121]:
df.head()

From Verse   To Verse  Votes  #www.openbible.info CC-BY 2020-11-02 Book  \
0  Gen.1.1    PRO.8.22   35    NaN                                    GEN   
1  Gen.1.1    EXO.31.18 -21    NaN                                    GEN   
2  Gen.1.1    JER.51.15  42    NaN                                    GEN   
3  Gen.1.1    REV.14.7   42    NaN                                    GEN   
4  Gen.1.1    ACT.14.15  39    NaN                                    GEN   

   chapter  Verse book_chapter  to2_verse     to_verse   to_verse3  \
0  1        1      GEN.1        30.0       PRO.8.22-30  Proverbs     
1  1        1      GEN.1       NaN         EXO.31.18    Exodus       
2  1        1      GEN.1       NaN         JER.51.15    Jeremiah     
3  1        1      GEN.1       NaN         REV.14.7     Revelation   
4  1        1      GEN.1       NaN         ACT.14.15    Acts         

     to_verse4  
0  PRO.8.22-30  
1  EXO.31.18    
2  JER.51.15    
3  REV.14.7     
4  ACT.14.15

In [122]:
df['to_verse4'] = df['to_verse4'].str.split('.').str[1]

In [123]:
df.head()

From Verse   To Verse  Votes  #www.openbible.info CC-BY 2020-11-02 Book  \
0  Gen.1.1    PRO.8.22   35    NaN                                    GEN   
1  Gen.1.1    EXO.31.18 -21    NaN                                    GEN   
2  Gen.1.1    JER.51.15  42    NaN                                    GEN   
3  Gen.1.1    REV.14.7   42    NaN                                    GEN   
4  Gen.1.1    ACT.14.15  39    NaN                                    GEN   

   chapter  Verse book_chapter  to2_verse     to_verse   to_verse3 to_verse4  
0  1        1      GEN.1        30.0       PRO.8.22-30  Proverbs    8         
1  1        1      GEN.1       NaN         EXO.31.18    Exodus      31        
2  1        1      GEN.1       NaN         JER.51.15    Jeremiah    51        
3  1        1      GEN.1       NaN         REV.14.7     Revelation  14        
4  1        1      GEN.1       NaN         ACT.14.15    Acts        14

In [124]:
df['to_verse5'] = df['to_verse']

In [125]:
df['to_verse5'] = df['to_verse5'].str.split('.').str[-1]

In [126]:
df.head()

From Verse   To Verse  Votes  #www.openbible.info CC-BY 2020-11-02 Book  \
0  Gen.1.1    PRO.8.22   35    NaN                                    GEN   
1  Gen.1.1    EXO.31.18 -21    NaN                                    GEN   
2  Gen.1.1    JER.51.15  42    NaN                                    GEN   
3  Gen.1.1    REV.14.7   42    NaN                                    GEN   
4  Gen.1.1    ACT.14.15  39    NaN                                    GEN   

   chapter  Verse book_chapter  to2_verse     to_verse   to_verse3 to_verse4  \
0  1        1      GEN.1        30.0       PRO.8.22-30  Proverbs    8          
1  1        1      GEN.1       NaN         EXO.31.18    Exodus      31         
2  1        1      GEN.1       NaN         JER.51.15    Jeremiah    51         
3  1        1      GEN.1       NaN         REV.14.7     Revelation  14         
4  1        1      GEN.1       NaN         ACT.14.15    Acts        14         

  to_verse5  
0  22-30     
1  18        
2  15        
3  7         
4  15

In [128]:
df['to_verse_display'] = df['to_verse3'] + ' ' + df['to_verse4'] +':' + df['to_verse5']

In [129]:
df.head(1000)

From Verse     To Verse  Votes  #www.openbible.info CC-BY 2020-11-02 Book  \
0    Gen.1.1    PRO.8.22     35    NaN                                    GEN   
1    Gen.1.1    EXO.31.18   -21    NaN                                    GEN   
2    Gen.1.1    JER.51.15    42    NaN                                    GEN   
3    Gen.1.1    REV.14.7     42    NaN                                    GEN   
4    Gen.1.1    ACT.14.15    39    NaN                                    GEN   
5    Gen.1.1    PSA.33.6     33    NaN                                    GEN   
6    Gen.1.1    ISA.51.16    34    NaN                                    GEN   
7    Gen.1.1    1JHN.1.1     29    NaN                                    GEN   
8    Gen.1.1    HEB.1.2      36    NaN                                    GEN   
9    Gen.1.1    PSA.136.5    40    NaN                                    GEN   
10   Gen.1.1    ISA.40.26    34    NaN                                    GEN   
11   Gen.1.1    PSA.134.3    32    NaN                                    GEN   
12   Gen.1.1    ROM.11.36    32    NaN                                    GEN   
13   Gen.1.1    PSA.102.25   37    NaN                                    GEN   
14   Gen.1.1    PRO.16.4     32    NaN                                    GEN   
15   Gen.1.1    1CO.8.6      38    NaN                                    GEN   
16   Gen.1.1    HEB.1.10     91    NaN                                    GEN   
17   Gen.1.1    PSA.121.2    34    NaN                                    GEN   
18   Gen.1.1    JER.32.17    44    NaN                                    GEN   
19   Gen.1.1    JER.10.12    40    NaN                                    GEN   
20   Gen.1.1    ISA.65.17    24    NaN                                    GEN   
21   Gen.1.1    PSA.96.5     32    NaN                                    GEN   
22   Gen.1.1    PSA.89.11    32    NaN                                    GEN   
23   Gen.1.1    REV.22.13    22    NaN                                    GEN   
24   Gen.1.1    REV.21.6     25    NaN                                    GEN   
25   Gen.1.1    JHN.1.1      163   NaN                                    GEN   
26   Gen.1.1    PSA.104.24   32    NaN                                    GEN   
27   Gen.1.1    1CH.16.26    27    NaN                                    GEN   
28   Gen.1.1    REV.10.6     33    NaN                                    GEN   
29   Gen.1.1    MRK.13.19    25    NaN                                    GEN   
30   Gen.1.1    ISA.40.28    37    NaN                                    GEN   
31   Gen.1.1    PSA.90.2     32    NaN                                    GEN   
32   Gen.1.1    PSA.115.15   40    NaN                                    GEN   
33   Gen.1.1    NEH.9.6      55    NaN                                    GEN   
34   Gen.1.1    ISA.44.24    49    NaN                                    GEN   
35   Gen.1.1    EXO.20.11    78    NaN                                    GEN   
36   Gen.1.1    JOB.38.4     83    NaN                                    GEN   
37   Gen.1.1    JOB.26.13    22    NaN                                    GEN   
38   Gen.1.1    MAT.11.25    5     NaN                                    GEN   
39   Gen.1.1    2PE.3.5      54    NaN                                    GEN   
40   Gen.1.1    HEB.11.3     141   NaN                                    GEN   
41   Gen.1.1    ACT.17.24    74    NaN                                    GEN   
42   Gen.1.1    COL.1.16     78    NaN                                    GEN   
43   Gen.1.1    PSA.33.9     40    NaN                                    GEN   
44   Gen.1.1    ECC.12.1     11    NaN                                    GEN   
45   Gen.1.1    REV.4.11     97    NaN                                    GEN   
46   Gen.1.1    ROM.1.19     29    NaN                                    GEN   
47   Gen.1.1    ISA.37.16    34    NaN                                    GEN   
48   Gen.1.1    PSA.8.3      35    

In [130]:
## save progress
df.to_csv("cross.csv", encoding='utf-8', index=False)

In [4]:
df = pd.read_csv('cross.csv')

In [133]:
columns = ['From Verse', 'To Verse', 'Votes', '#www.openbible.info CC-BY 2020-11-02', 'to2_verse', 'to_verse3', 'to_verse4', 'to_verse5']
df.drop(columns, inplace=True, axis=1)

In [136]:
df.columns = [["book", "chapter", "verse", "book_chapter", "to_verse", "to_verse_display"]]

In [5]:
df.head(10000)

book  chapter  verse book_chapter       to_verse         to_verse_display
0     GEN  1        1      GEN.1        PRO.8.22-30    Proverbs 8:22-30       
1     GEN  1        1      GEN.1        EXO.31.18      Exodus 31:18           
2     GEN  1        1      GEN.1        JER.51.15      Jeremiah 51:15         
3     GEN  1        1      GEN.1        REV.14.7       Revelation 14:7        
4     GEN  1        1      GEN.1        ACT.14.15      Acts 14:15             
5     GEN  1        1      GEN.1        PSA.33.6       Psalms 33:6            
6     GEN  1        1      GEN.1        ISA.51.16      Isaiah 51:16           
7     GEN  1        1      GEN.1        1JHN.1.1       1JHN 1:1               
8     GEN  1        1      GEN.1        HEB.1.2        Hebrews 1:2            
9     GEN  1        1      GEN.1        PSA.136.5      Psalms 136:5           
10    GEN  1        1      GEN.1        ISA.40.26      Isaiah 40:26           
11    GEN  1        1      GEN.1        PSA.134.3      Psalms 134:3           
12    GEN  1        1      GEN.1        ROM.11.36      Romans 11:36           
13    GEN  1        1      GEN.1        PSA.102.25     Psalms 102:25          
14    GEN  1        1      GEN.1        PRO.16.4       Proverbs 16:4          
15    GEN  1        1      GEN.1        1CO.8.6        1 Corinthians 8:6      
16    GEN  1        1      GEN.1        HEB.1.10       Hebrews 1:10           
17    GEN  1        1      GEN.1        PSA.121.2      Psalms 121:2           
18    GEN  1        1      GEN.1        JER.32.17      Jeremiah 32:17         
19    GEN  1        1      GEN.1        JER.10.12      Jeremiah 10:12         
20    GEN  1        1      GEN.1        ISA.65.17      Isaiah 65:17           
21    GEN  1        1      GEN.1        PSA.96.5       Psalms 96:5            
22    GEN  1        1      GEN.1        PSA.89.11-12   Psalms 89:11-12        
23    GEN  1        1      GEN.1        REV.22.13      Revelation 22:13       
24    GEN  1        1      GEN.1        REV.21.6       Revelation 21:6        
25    GEN  1        1      GEN.1        JHN.1.1-3      John 1:1-3             
26    GEN  1        1      GEN.1        PSA.104.24     Psalms 104:24          
27    GEN  1        1      GEN.1        1CH.16.26      1 Chronicles 16:26     
28    GEN  1        1      GEN.1        REV.10.6       Revelation 10:6        
29    GEN  1        1      GEN.1        MRK.13.19      Mark 13:19             
30    GEN  1        1      GEN.1        ISA.40.28      Isaiah 40:28           
31    GEN  1        1      GEN.1        PSA.90.2       Psalms 90:2            
32    GEN  1        1      GEN.1        PSA.115.15     Psalms 115:15          
33    GEN  1        1      GEN.1        NEH.9.6        Nehemiah 9:6           
34    GEN  1        1      GEN.1        ISA.44.24      Isaiah 44:24           
35    GEN  1        1      GEN.1        EXO.20.11      Exodus 20:11           
36    GEN  1        1      GEN.1        JOB.38.4       Job 38:4               
37    GEN  1        1      GEN.1        JOB.26.13      Job 26:13              
38    GEN  1        1      GEN.1        MAT.11.25      Matthew 11:25          
39    GEN  1        1      GEN.1        2PE.3.5        2 Peter 3:5            
40    GEN  1        1      GEN.1        HEB.11.3       Hebrews 11:3           
41    GEN  1        1      GEN.1        ACT.17.24      Acts 17:24             
42    GEN  1        1      GEN.1        COL.1.16-17    Colossians 1:16-17     
43    GEN  1        1      GEN.1        PSA.33.9       Psalms 33:9            
44    GEN  1        1      GEN.1        ECC.12.1       Ecclesiastes 12:1      
45    GEN  1        1      GEN.1        REV.4.11       Revelation 4:11        
46    GEN  1        1      GEN.1        ROM.1.19-20    Romans 1:19-20         
47    GEN  1        1      GEN.1        ISA.37.16      Isaiah 37:16           
48    GEN  1        1      GEN.1        PSA.8.3        Psalms 8:3             
49    GEN  1        1      GEN.1        PSA.124.8      

In [3]:
## save progress
df.to_csv("cross.csv", encoding='utf-8', index=False)

NameError: name 'df' is not defined

In [139]:
df = pd.read_csv('cross.csv')

In [295]:
df.head(100)

book  chapter  verse book_chapter      to_verse    to_verse_display
0   GEN  1        1      GEN.1        PRO.8.22-30   Proverbs 8:22-30  
1   GEN  1        1      GEN.1        EXO.31.18     Exodus 31:18      
2   GEN  1        1      GEN.1        JER.51.15     Jeremiah 51:15    
3   GEN  1        1      GEN.1        REV.14.7      Revelation 14:7   
4   GEN  1        1      GEN.1        ACT.14.15     Acts 14:15        
5   GEN  1        1      GEN.1        PSA.33.6      Psalms 33:6       
6   GEN  1        1      GEN.1        ISA.51.16     Isaiah 51:16      
7   GEN  1        1      GEN.1        1JHN.1.1      1JHN 1:1          
8   GEN  1        1      GEN.1        HEB.1.2       Hebrews 1:2       
9   GEN  1        1      GEN.1        PSA.136.5     Psalms 136:5      
10  GEN  1        1      GEN.1        ISA.40.26     Isaiah 40:26      
11  GEN  1        1      GEN.1        PSA.134.3     Psalms 134:3      
12  GEN  1        1      GEN.1        ROM.11.36     Romans 11:36      
13  GEN  1        1      GEN.1        PSA.102.25    Psalms 102:25     
14  GEN  1        1      GEN.1        PRO.16.4      Proverbs 16:4     
15  GEN  1        1      GEN.1        1CO.8.6       1 Corinthians 8:6 
16  GEN  1        1      GEN.1        HEB.1.10      Hebrews 1:10      
17  GEN  1        1      GEN.1        PSA.121.2     Psalms 121:2      
18  GEN  1        1      GEN.1        JER.32.17     Jeremiah 32:17    
19  GEN  1        1      GEN.1        JER.10.12     Jeremiah 10:12    
20  GEN  1        1      GEN.1        ISA.65.17     Isaiah 65:17      
21  GEN  1        1      GEN.1        PSA.96.5      Psalms 96:5       
22  GEN  1        1      GEN.1        PSA.89.11-12  Psalms 89:11-12   
23  GEN  1        1      GEN.1        REV.22.13     Revelation 22:13  
24  GEN  1        1      GEN.1        REV.21.6      Revelation 21:6   
25  GEN  1        1      GEN.1        JHN.1.1-3     John 1:1-3        
26  GEN  1        1      GEN.1        PSA.104.24    Psalms 104:24     
27  GEN  1        1      GEN.1        1CH.16.26     1 Chronicles 16:26
28  GEN  1        1      GEN.1        REV.10.6      Revelation 10:6   
29  GEN  1        1      GEN.1        MRK.13.19     Mark 13:19        
30  GEN  1        1      GEN.1        ISA.40.28     Isaiah 40:28      
31  GEN  1        1      GEN.1        PSA.90.2      Psalms 90:2       
32  GEN  1        1      GEN.1        PSA.115.15    Psalms 115:15     
33  GEN  1        1      GEN.1        NEH.9.6       Nehemiah 9:6      
34  GEN  1        1      GEN.1        ISA.44.24     Isaiah 44:24      
35  GEN  1        1      GEN.1        EXO.20.11     Exodus 20:11      
36  GEN  1        1      GEN.1        JOB.38.4      Job 38:4          
37  GEN  1        1      GEN.1        JOB.26.13     Job 26:13         
38  GEN  1        1      GEN.1        MAT.11.25     Matthew 11:25     
39  GEN  1        1      GEN.1        2PE.3.5       2 Peter 3:5       
40  GEN  1        1      GEN.1        HEB.11.3      Hebrews 11:3      
41  GEN  1        1      GEN.1        ACT.17.24     Acts 17:24        
42  GEN  1        1      GEN.1        COL.1.16-17   Colossians 1:16-17
43  GEN  1        1      GEN.1        PSA.33.9      Psalms 33:9       
44  GEN  1        1      GEN.1        ECC.12.1      Ecclesiastes 12:1 
45  GEN  1        1      GEN.1        REV.4.11      Revelation 4:11   
46  GEN  1        1      GEN.1        ROM.1.19-20   Romans 1:19-20    
47  GEN  1        1      GEN.1        ISA.37.16     Isaiah 37:16      
48  GEN  1        1      GEN.1        PSA.8.3       Psalms 8:3        
49  GEN  1        1      GEN.1        PSA.124.8     Psalms 124:8      
50  GEN  1        1      GEN.1        PSA.104.30    Psalms 104:30     
51  GEN  1        1      GEN.1        REV.3.14      Revelation 3:14   
52  GEN  1        1      GEN.1        PSA.146.6     Psalms 146:6      
53  GEN  1        1      GEN.1        HEB.3.4       Hebrews 3:4       
54  GEN  1        1      GEN.1        ISA.42.5      Isaiah 42:5       
55  GEN  1        1      GE

In [58]:
asd = df[(df.book_chapter=='GEN.1')][['verse', 'to_verse', 'to_verse_display']]
arr = asd.verse.unique()
asd

verse       to_verse      to_verse_display
0    1      PRO.8.22-30    Proverbs 8:22-30    
1    1      EXO.31.18      Exodus 31:18        
2    1      JER.51.15      Jeremiah 51:15      
3    1      REV.14.7       Revelation 14:7     
4    1      ACT.14.15      Acts 14:15          
5    1      PSA.33.6       Psalms 33:6         
6    1      ISA.51.16      Isaiah 51:16        
7    1      1JHN.1.1       1JHN 1:1            
8    1      HEB.1.2        Hebrews 1:2         
9    1      PSA.136.5      Psalms 136:5        
10   1      ISA.40.26      Isaiah 40:26        
11   1      PSA.134.3      Psalms 134:3        
12   1      ROM.11.36      Romans 11:36        
13   1      PSA.102.25     Psalms 102:25       
14   1      PRO.16.4       Proverbs 16:4       
15   1      1CO.8.6        1 Corinthians 8:6   
16   1      HEB.1.10       Hebrews 1:10        
17   1      PSA.121.2      Psalms 121:2        
18   1      JER.32.17      Jeremiah 32:17      
19   1      JER.10.12      Jeremiah 10:12      
20   1      ISA.65.17      Isaiah 65:17        
21   1      PSA.96.5       Psalms 96:5         
22   1      PSA.89.11-12   Psalms 89:11-12     
23   1      REV.22.13      Revelation 22:13    
24   1      REV.21.6       Revelation 21:6     
25   1      JHN.1.1-3      John 1:1-3          
26   1      PSA.104.24     Psalms 104:24       
27   1      1CH.16.26      1 Chronicles 16:26  
28   1      REV.10.6       Revelation 10:6     
29   1      MRK.13.19      Mark 13:19          
30   1      ISA.40.28      Isaiah 40:28        
31   1      PSA.90.2       Psalms 90:2         
32   1      PSA.115.15     Psalms 115:15       
33   1      NEH.9.6        Nehemiah 9:6        
34   1      ISA.44.24      Isaiah 44:24        
35   1      EXO.20.11      Exodus 20:11        
36   1      JOB.38.4       Job 38:4            
37   1      JOB.26.13      Job 26:13           
38   1      MAT.11.25      Matthew 11:25       
39   1      2PE.3.5        2 Peter 3:5         
40   1      HEB.11.3       Hebrews 11:3        
41   1      ACT.17.24      Acts 17:24          
42   1      COL.1.16-17    Colossians 1:16-17  
43   1      PSA.33.9       Psalms 33:9         
44   1      ECC.12.1       Ecclesiastes 12:1   
45   1      REV.4.11       Revelation 4:11     
46   1      ROM.1.19-20    Romans 1:19-20      
47   1      ISA.37.16      Isaiah 37:16        
48   1      PSA.8.3        Psalms 8:3          
49   1      PSA.124.8      Psalms 124:8        
50   1      PSA.104.30     Psalms 104:30       
51   1      REV.3.14       Revelation 3:14     
52   1      PSA.146.6      Psalms 146:6        
53   1      HEB.3.4        Hebrews 3:4         
54   1      ISA.42.5       Isaiah 42:5         
55   1      ISA.45.18      Isaiah 45:18        
56   1      ACT.4.24       Acts 4:24           
57   1      EPH.3.9        Ephesians 3:9       
58   1      ZEC.12.1       Zechariah 12:1      
59   1      ISA.51.13      Isaiah 51:13        
60   1      PRO.3.19       Proverbs 3:19       
61   1      PSA.148.4-5    Psalms 148:4-5      
62   2      ISA.45.18      Isaiah 45:18        
63   2      JER.4.23       Jeremiah 4:23       
64   2      NAM.2.10       Nahum 2:10          
65   2      PSA.104.30     Psalms 104:30       
66   2      JOB.26.7       Job 26:7            
67   2      JOB.26.14      Job 26:14           
68   2      ISA.40.12-14   Isaiah 40:12-14     
69   2      PSA.33.6       Psalms 33:6         
70   3      PSA.33.9       Psalms 33:9         
71   3      MAT.8.3        Matthew 8:3         
72   3      1JHN.1.5       1JHN 1:5            
73   3      1JHN.2.8       1JHN 2:8            
74   3      JOB.36.30      Job 36:30           
75   3      JOB.38.19      Job 38:19           
76   3      EPH.5.14       Ephesians 5:14      
77   3      PSA.33.6       Psalms 33:6         
78   3      PSA.148.5      Psalms 148:5        
79   3      PSA.97.11      Psalms 97:11        
80   3      EPH.5.8        Ephesians 5:8       
81   3      JHN.1.9        John 1:9            
82   3      PSA.118.2

In [76]:
asd = df[(df.book_chapter=='GEN.1')][['verse', 'to_verse', 'to_verse_display']]
arr = asd.verse.unique()
asd
master_array = []
for item in arr:
    tt = asd[(asd.verse==item)]['to_verse_display']
    test_arr = []
    for item2 in tt:
        test_arr.append(item2)
    case = {"Verse:": item, "Verses:": test_arr}
    master_array.append(case)

In [84]:
master_array

[{'Verse:': 1,
  'Verses:': ['Proverbs 8:22-30',
   'Exodus 31:18',
   'Jeremiah 51:15',
   'Revelation 14:7',
   'Acts 14:15',
   'Psalms 33:6',
   'Isaiah 51:16',
   '1JHN 1:1',
   'Hebrews 1:2',
   'Psalms 136:5',
   'Isaiah 40:26',
   'Psalms 134:3',
   'Romans 11:36',
   'Psalms 102:25',
   'Proverbs 16:4',
   '1 Corinthians 8:6',
   'Hebrews 1:10',
   'Psalms 121:2',
   'Jeremiah 32:17',
   'Jeremiah 10:12',
   'Isaiah 65:17',
   'Psalms 96:5',
   'Psalms 89:11-12',
   'Revelation 22:13',
   'Revelation 21:6',
   'John 1:1-3',
   'Psalms 104:24',
   '1 Chronicles 16:26',
   'Revelation 10:6',
   'Mark 13:19',
   'Isaiah 40:28',
   'Psalms 90:2',
   'Psalms 115:15',
   'Nehemiah 9:6',
   'Isaiah 44:24',
   'Exodus 20:11',
   'Job 38:4',
   'Job 26:13',
   'Matthew 11:25',
   '2 Peter 3:5',
   'Hebrews 11:3',
   'Acts 17:24',
   'Colossians 1:16-17',
   'Psalms 33:9',
   'Ecclesiastes 12:1',
   'Revelation 4:11',
   'Romans 1:19-20',
   'Isaiah 37:16',
   'Psalms 8:3',
   'Psalms 1

In [73]:
test = asd[(asd.verse==1)]['to_verse_display']
test_arr = []
for item in test:
    test_arr.append(item)

['Psalms 104:24',
 'Genesis 1:8',
 'Genesis 1:23',
 'Genesis 1:5',
 'Exodus 20:11',
 'Genesis 1:13',
 'Psalms 19:1-2',
 'Psalms 104:31',
 'Job 38:7',
 'Lamentations 3:38',
 'Genesis 1:19',
 '1 Timothy 4:4',
 'Genesis 2:2']